# Phase 1: LLAMA + MBPP Dataset Results Inspection

This notebook inspects Phase 1 LLAMA results to verify:
- Dataset files created correctly
- Model used (LLAMA-3.1-8B)
- Prompts formatted correctly
- Code generation working
- Evaluation results (pass/fail)
- Activations captured (31 layers)

In [12]:
import pandas as pd
import os
from pathlib import Path
import glob
import json
import numpy as np

# Set pandas display options to show FULL content
pd.set_option('display.max_colwidth', None)  # Show full column content (NO LIMITS)
pd.set_option('display.max_columns', None)   # Show all columns
pd.set_option('display.width', None)         # Don't wrap to multiple lines
pd.set_option('display.max_rows', None)      # Show ALL rows (no limit)

print("✅ Pandas display options set to show FULL content")

✅ Pandas display options set to show FULL content


In [13]:
# Auto-discovery of Phase 1 LLAMA data
datasets_dir = "../data/phase1_0_llama/"
pattern = os.path.join(datasets_dir, "dataset_*.parquet")
matching_files = glob.glob(pattern)

if matching_files:
    # Sort by timestamp (filename)
    matching_files.sort(reverse=True)  # Most recent first
    print("=" * 80)
    print("PHASE 1: LLAMA + MBPP DATASET GENERATION")
    print("=" * 80)
    print(f"\n🔍 Found {len(matching_files)} dataset file(s)")
    for file in matching_files:
        file_size = os.path.getsize(file) / 1024  # KB
        print(f"  📁 {Path(file).name} ({file_size:.2f} KB)")
    
    # Use most recent file
    latest_file = matching_files[0]
    print(f"\n📄 Using most recent: {Path(latest_file).name}")
else:
    raise FileNotFoundError(f"❌ No dataset files found in {datasets_dir}")

PHASE 1: LLAMA + MBPP DATASET GENERATION

🔍 Found 1 dataset file(s)
  📁 dataset_sae_20251126_145021.parquet (281.28 KB)

📄 Using most recent: dataset_sae_20251126_145021.parquet


In [14]:
# Check activations directory
activations_dir = Path(datasets_dir) / "activations"

print("\n" + "=" * 80)
print("ACTIVATIONS DIRECTORY")
print("=" * 80)

if activations_dir.exists():
    print(f"\n✅ Activations directory exists: {activations_dir}")
    
    # Check subdirectories
    subdirs = [d for d in activations_dir.iterdir() if d.is_dir()]
    print(f"\n📁 Subdirectories ({len(subdirs)}):")
    for subdir in subdirs:
        files = list(subdir.glob("*.npz"))
        print(f"  - {subdir.name}/: {len(files)} activation files")
        if files:
            print(f"    Sample: {files[0].name}")
            
            # Check activation dimensions for LLAMA (should be 4096)
            sample_data = np.load(files[0])
            for key in sample_data.files:
                print(f"    Shape ({key}): {sample_data[key].shape}")
else:
    print(f"\n⚠️  Activations directory not found: {activations_dir}")


ACTIVATIONS DIRECTORY

✅ Activations directory exists: ../data/phase1_0_llama/activations

📁 Subdirectories (2):
  - incorrect/: 7626 activation files
    Sample: 926_layer_31.npz
    Shape (layer_31): (1, 4096)
  - correct/: 7533 activation files
    Sample: 811_layer_15.npz
    Shape (layer_15): (1, 4096)


In [15]:
# Load and display dataset
print(f"\n{'=' * 80}")
print(f"DATASET CONTENTS")
print("=" * 80)

df = pd.read_parquet(latest_file)

# Basic stats
print(f"\n📊 Statistics:")
print(f"  - Total records: {len(df)}")
print(f"  - Columns: {list(df.columns)}")

# Pass rate
if 'test_passed' in df.columns:
    n_passed = df['test_passed'].sum()
    pass_rate = n_passed / len(df) * 100
    print(f"\n✅ Pass Rate:")
    print(f"  - Passed: {n_passed}/{len(df)} ({pass_rate:.2f}%)")
    print(f"  - Failed: {len(df) - n_passed}/{len(df)} ({100 - pass_rate:.2f}%)")

# Generation time stats
if 'generation_time' in df.columns:
    print(f"\n⏱️  Generation Time:")
    print(f"  - Mean: {df['generation_time'].mean():.2f}s")
    print(f"  - Median: {df['generation_time'].median():.2f}s")
    print(f"  - Min: {df['generation_time'].min():.2f}s")
    print(f"  - Max: {df['generation_time'].max():.2f}s")


DATASET CONTENTS

📊 Statistics:
  - Total records: 489
  - Columns: ['task_id', 'text', 'code', 'test_list', 'cyclomatic_complexity', 'text_x', 'code_x', 'test_list_x', 'cyclomatic_complexity_x', 'text_y', 'code_y', 'test_list_y', 'cyclomatic_complexity_y', 'generated_code', 'raw_output', 'test_passed']

✅ Pass Rate:
  - Passed: 243/489 (49.69%)
  - Failed: 246/489 (50.31%)


In [16]:
# Display all records
print(f"\n{'=' * 80}")
print(f"ALL RECORDS:")
print("=" * 80)
display(df)


ALL RECORDS:


task_id  \
0          2   
1          3   
2          4   
3          6   
4          7   
5          9   
6         11   
7         12   
8         13   
9         15   
10        16   
11        19   
12        23   
13        25   
14        26   
15        30   
16        31   
17        32   
18        33   
19        34   
20        35   
21        36   
22        38   
23        39   
24        41   
25        44   
26        45   
27        46   
28        48   
29        49   
30        54   
31        56   
32        60   
33        62   
34        63   
35        64   
36        66   
37        70   
38        71   
39        73   
40        76   
41        77   
42        79   
43        81   
44        85   
45        87   
46        90   
47        96   
48        97   
49        98   
50       101   
51       102   
52       103   
53       104   
54       107   
55       108   
56       110   
57       112   
58       117   
59       118   
60       120   
61       121   
62       124   
63       125   
64       126   
65       127   
66       128   
67       129   
68       134   
69       135   
70       136   
71       138   
72       140   
73       141   
74       142   
75       143   
76       145   
77       149   
78       150   
79       151   
80       152   
81       153   
82       156   
83       160   
84       162   
85       163   
86       164   
87       165   
88       166   
89       170   
90       172   
91       173   
92       174   
93       175   
94       176   
95       177   
96       179   
97       182   
98       183   
99       184   
100      186   
101      188   
102      191   
103      192   
104      193   
105      195   
106      197   
107      202   
108      204   
109      206   
110      207   
111      208   
112      209   
113      211   
114      214   
115      217   
116      218   
117      219   
118      220   
119      221   
120      224   
121      225   
122      228   
123      231   
124      232   
125      235   
126      237   
127      241   
128      242   
129      243   
130      244   
131      247   
132      248   
133      250   
134      251   
135      260   
136      262   
137      263   
138      266   
139      267   
140      269   
141      272   
142      273   
143      274   
144      276   
145      280   
146      283   
147      289   
148      291   
149      294   
150      298   
151      299   
152      304   
153      306   
154      308   
155      309   
156      312   
157      315   
158      317   
159      326   
160      327   
161      330   
162      331   
163      333   
164      335   
165      336   
166      339   
167      341   
168      345   
169      346   
170      347   
171      348   
172      349   
173      351   
174      352   
175      353   
176      354   
177      356   
178      357   
179      358   
180      360   
181      362   
182      363   
183      369   
184      370   
185      375   
186      378   
187      379   
188      381   
189      382   
190      384   
191      385   
192      386   
193      388   
194      389   
195      391   
196      392   
197      395   
198      396   
199      397   
200      398   
201      404   
202      406   
203      408   
204      412   
205      414   
206      417   
207      419   
208      420   
209      422   
210      426   
211      427   
212      428   
213      429   
214      430   
215      433   
216      434   
217      435   
218      439   
219      440   
220      442   
221      443   
222      446   
223      447   
224      448   
225      451   
226      452   
227      454   
228      456   
229      457   
230      458   
231      459   
232      462   
233      463   
234      467   
235      468   
236      469   
237      470   
238      475   
239      476   
240      477   
241      478   
242      479   
243      481   
244      484   
245      491   
246      492   
247      494   
248      495   
249  

In [ ]:
# Show sample correct and incorrect generations
print("\n" + "=" * 80)
print("SAMPLE CORRECT GENERATION")
print("=" * 80)

if 'test_passed' in df.columns and df['test_passed'].any():
    correct_sample = df[df['test_passed'] == True].iloc[0]
    print(f"\n📋 Task ID: {correct_sample.get('task_id', 'N/A')}")
    print(f"\n📝 Prompt:")
    print(correct_sample.get('prompt', 'N/A')[:500] + "..." if len(str(correct_sample.get('prompt', ''))) > 500 else correct_sample.get('prompt', 'N/A'))
    print(f"\n💻 Generated Code:")
    print(correct_sample.get('generated_code', 'N/A'))
else:
    print("\n⚠️  No correct generations found")

In [ ]:
# Show sample incorrect generation
print("\n" + "=" * 80)
print("SAMPLE INCORRECT GENERATION")
print("=" * 80)

if 'test_passed' in df.columns and (~df['test_passed']).any():
    incorrect_sample = df[df['test_passed'] == False].iloc[0]
    print(f"\n📋 Task ID: {incorrect_sample.get('task_id', 'N/A')}")
    print(f"\n📝 Prompt:")
    print(incorrect_sample.get('prompt', 'N/A')[:500] + "..." if len(str(incorrect_sample.get('prompt', ''))) > 500 else incorrect_sample.get('prompt', 'N/A'))
    print(f"\n💻 Generated Code:")
    print(incorrect_sample.get('generated_code', 'N/A'))
    if 'error_message' in incorrect_sample and incorrect_sample['error_message']:
        print(f"\n❌ Error:")
        print(incorrect_sample['error_message'])
else:
    print("\n⚠️  No incorrect generations found")

In [ ]:
# Summary
print("\n" + "=" * 80)
print("OVERALL SUMMARY")
print("=" * 80)

print(f"\n📊 Dataset file: {Path(latest_file).name}")
print(f"📊 Total records: {len(df)}")
if 'test_passed' in df.columns:
    print(f"✅ Pass rate: {df['test_passed'].sum()}/{len(df)} ({df['test_passed'].mean()*100:.2f}%)")
print(f"📁 Activations exist: {'✅' if activations_dir.exists() else '❌'}")

# Check if activations have correct dimension for LLAMA (4096)
if activations_dir.exists():
    task_acts_dir = activations_dir / "task_activations"
    if task_acts_dir.exists():
        sample_files = list(task_acts_dir.glob("*.npz"))[:1]
        if sample_files:
            data = np.load(sample_files[0])
            for key in data.files:
                dim = data[key].shape[-1]
                expected = 4096  # LLAMA hidden size
                status = '✅' if dim == expected else '❌'
                print(f"{status} Activation dimension: {dim} (expected {expected} for LLAMA)")

print("\n🎉 Phase 1 LLAMA results inspection complete!")